In [363]:
import polars as pl
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
from datetime import datetime as dt
import datetime
import pytz

In [364]:
boxes = pl.read_parquet('predictions.parquet')
img_index = pl.read_parquet('image_index.parquet')

In [365]:
img_index.head()

shape: (5, 5)
┌───────────────────────────┬─────────────┬────────────┬────────────────┬──────────────────────────┐
│ path                      ┆ date_folder ┆ timestamp  ┆ location       ┆ image_id                 │
│ ---                       ┆ ---         ┆ ---        ┆ ---            ┆ ---                      │
│ str                       ┆ str         ┆ i64        ┆ str            ┆ str                      │
╞═══════════════════════════╪═════════════╪════════════╪════════════════╪══════════════════════════╡
│ ../image_downloader/image ┆ 2025-04-20  ┆ 1745143200 ┆ MC_DHPOS       ┆ 1745143200_MC_DHPOS      │
│ s/202…                    ┆             ┆            ┆                ┆                          │
│ ../image_downloader/image ┆ 2025-04-20  ┆ 1745143200 ┆ MC_DHService1  ┆ 1745143200_MC_DHService1 │
│ s/202…                    ┆             ┆            ┆                ┆                          │
│ ../image_downloader/image ┆ 2025-04-20  ┆ 1745143200 ┆ MC_DHService2  ┆ 1745143200_MC_DHService2 │
│ s/202…                    ┆             ┆            ┆                ┆                          │
│ ../image_downloader/image ┆ 2025-04-20  ┆ 1745143200 ┆ MC_DHSmoothies ┆ 1745143200_MC_DHSmoothie │
│ s/202…                    ┆             ┆            ┆                ┆ s                        │
│ ../image_downloader/image ┆ 2025-04-20  ┆ 1745143200 ┆ MC_Exit1       ┆ 1745143200_MC_Exit1      │
│ s/202…                    ┆             ┆            ┆                ┆                          │
└───────────────────────────┴─────────────┴────────────┴────────────────┴──────────────────────────┘

In [366]:
img_index = img_index.filter(
    (pl.col('date_folder') >= '2025-03-17') &
    (pl.col('date_folder') <= '2025-04-13')
)
img_index = img_index.with_columns(
    dt = pl.from_epoch('timestamp', time_unit='s').dt.convert_time_zone('America/New_York')
)
img_index = img_index.with_columns(
    week = pl.col('dt').dt.week()
)

In [367]:
img_index.head()

shape: (5, 7)
┌────────────────┬─────────────┬────────────┬───────────────┬───────────────┬───────────────┬──────┐
│ path           ┆ date_folder ┆ timestamp  ┆ location      ┆ image_id      ┆ dt            ┆ week │
│ ---            ┆ ---         ┆ ---        ┆ ---           ┆ ---           ┆ ---           ┆ ---  │
│ str            ┆ str         ┆ i64        ┆ str           ┆ str           ┆ datetime[μs,  ┆ i8   │
│                ┆             ┆            ┆               ┆               ┆ America/New_Y ┆      │
│                ┆             ┆            ┆               ┆               ┆ ork]          ┆      │
╞════════════════╪═════════════╪════════════╪═══════════════╪═══════════════╪═══════════════╪══════╡
│ ../image_downl ┆ 2025-03-19  ┆ 1742390088 ┆ NH_DHDeli     ┆ 1742390088_NH ┆ 2025-03-19    ┆ 12   │
│ oader/images/2 ┆             ┆            ┆               ┆ _DHDeli       ┆ 09:14:48 EDT  ┆      │
│ 02…            ┆             ┆            ┆               ┆               ┆               ┆      │
│ ../image_downl ┆ 2025-03-19  ┆ 1742389519 ┆ MC_Exit2      ┆ 1742389519_MC ┆ 2025-03-19    ┆ 12   │
│ oader/images/2 ┆             ┆            ┆               ┆ _Exit2        ┆ 09:05:19 EDT  ┆      │
│ 02…            ┆             ┆            ┆               ┆               ┆               ┆      │
│ ../image_downl ┆ 2025-03-19  ┆ 1742384680 ┆ MC_PO         ┆ 1742384680_MC ┆ 2025-03-19    ┆ 12   │
│ oader/images/2 ┆             ┆            ┆               ┆ _PO           ┆ 07:44:40 EDT  ┆      │
│ 02…            ┆             ┆            ┆               ┆               ┆               ┆      │
│ ../image_downl ┆ 2025-03-19  ┆ 1742380850 ┆ MC_DHService1 ┆ 1742380850_MC ┆ 2025-03-19    ┆ 12   │
│ oader/images/2 ┆             ┆            ┆               ┆ _DHService1   ┆ 06:40:50 EDT  ┆      │
│ 02…            ┆             ┆            ┆               ┆               ┆               ┆      │
│ ../image_downl ┆ 2025-03-19  ┆ 1742422697 ┆ NH_DHGym      ┆ 1742422697_NH ┆ 2025-03-19    ┆ 12   │
│ oader/images/2 ┆             ┆            ┆               ┆ _DHGym        ┆ 18:18:17 EDT  ┆      │
│ 02…            ┆             ┆            ┆               ┆               ┆               ┆      │
└────────────────┴─────────────┴────────────┴───────────────┴───────────────┴───────────────┴──────┘

In [368]:
img_index.group_by('week').len()

shape: (4, 2)
┌──────┬────────┐
│ week ┆ len    │
│ ---  ┆ ---    │
│ i8   ┆ u32    │
╞══════╪════════╡
│ 13   ┆ 240547 │
│ 15   ┆ 242268 │
│ 12   ┆ 240470 │
│ 14   ┆ 241471 │
└──────┴────────┘

In [369]:
counts = boxes.group_by('image_id').len()
traffic = img_index.join(counts, on='image_id', how='left')
traffic = traffic.rename({'len': 'count'})
traffic = traffic.with_columns(
    pl.col('count').fill_null(0)
)

In [370]:
import altair as alt

traffic.group_by(
    pl.col('dt').dt.date()
).agg(
    pl.col('count').sum().alias('total_count'),
).sort(
    pl.col('dt').dt.date()
).plot.line(
    x=alt.X('dt:T', title='Date'),
    y=alt.Y('total_count:Q', title='Total Count'),
).properties(
    width=900,
    height=400
)

alt.Chart(...)

In [371]:
traffic.group_by(
    [pl.col('location'), pl.col('dt').dt.date()]
).agg(
    (pl.col('count') > 0).sum().alias('non_zero_count'),
).filter(
    pl.col('non_zero_count') > 0
)

shape: (290, 3)
┌───────────────┬────────────┬────────────────┐
│ location      ┆ dt         ┆ non_zero_count │
│ ---           ┆ ---        ┆ ---            │
│ str           ┆ date       ┆ u32            │
╞═══════════════╪════════════╪════════════════╡
│ MC_Turnstiles ┆ 2025-03-25 ┆ 1805           │
│ NH_DHPOS1     ┆ 2025-04-09 ┆ 1370           │
│ MC_DHService1 ┆ 2025-03-22 ┆ 1821           │
│ NH_DHPOS2     ┆ 2025-04-05 ┆ 503            │
│ NH_DHService3 ┆ 2025-04-09 ┆ 796            │
│ …             ┆ …          ┆ …              │
│ MC_DHService2 ┆ 2025-03-31 ┆ 1801           │
│ MC_DHService2 ┆ 2025-04-04 ┆ 1377           │
│ MC_DHService2 ┆ 2025-04-02 ┆ 1822           │
│ NH_DHDeli     ┆ 2025-04-05 ┆ 53             │
│ NH_DHGym      ┆ 2025-04-04 ┆ 762            │
└───────────────┴────────────┴────────────────┘

In [372]:
import json
with open('../image_downloader/secrets/cameras.json') as f:
    cams = json.load(f)

for cam in cams:
    cam['location'] = cam['url'].split('/')[-1].split('.')[0]

cams = pl.DataFrame(cams)

cams = cams.rename({'name': 'location_name'})
cams = cams.drop(['class'])

traffic = traffic.join(cams, on='location', how='left')

In [373]:
for r in cams.iter_rows():
    print(r)

('Mount Carmel Dining Hall Checkout', 'https://checkthewait.qu.edu/cams/MC_DHPOS.jpg', 'MC_DHPOS')
('Mount Carmel Dining Hall', 'https://checkthewait.qu.edu/cams/MC_DHService1.jpg', 'MC_DHService1')
('Mount Carmel Dining Hall', 'https://checkthewait.qu.edu/cams/MC_DHService2.jpg', 'MC_DHService2')
('Mount Carmel Dining Hall Smoothies', 'https://checkthewait.qu.edu/cams/MC_DHSmoothies.jpg', 'MC_DHSmoothies')
('Mount Carmel Exit', 'https://checkthewait.qu.edu/cams/MC_Exit1.jpg', 'MC_Exit1')
('Mount Carmel Exit', 'https://checkthewait.qu.edu/cams/MC_Exit2.jpg', 'MC_Exit2')
('Mount Carmel Piazza', 'https://checkthewait.qu.edu/cams/MC_Piazza.jpg', 'MC_Piazza')
('Mount Carmel Post Office', 'https://checkthewait.qu.edu/cams/MC_PO.jpg', 'MC_PO')
('Mount Carmel Post Office', 'https://checkthewait.qu.edu/cams/MC_PO2.jpg', 'MC_PO2')
('Mount Carmel Recreation Lobby Shake Smart Line', 'https://checkthewait.qu.edu/cams/MC_RLSHAKE.jpg', 'MC_RLSHAKE')
('Mount Carmel Turnstiles', 'https://checkthewait.

In [374]:
# "MC_PO2"	2025-04-10	

loc = 'MC_PO2'
day = dt(2025, 4, 10)

t = traffic.filter(
    (pl.col('location') == loc) &
    (pl.col('dt').dt.date() == day.date())
)

c = t.group_by(
    # pl.col('dt').dt.hour()
    pl.col('dt').dt.truncate('5m')
).agg(
    pl.all().sort_by('count').last()
)

In [375]:
c.sort('dt').head()

shape: (5, 10)
┌─────────────┬─────────────┬────────────┬────────────┬───┬──────┬───────┬────────────┬────────────┐
│ dt          ┆ path        ┆ date_folde ┆ timestamp  ┆ … ┆ week ┆ count ┆ location_n ┆ url        │
│ ---         ┆ ---         ┆ r          ┆ ---        ┆   ┆ ---  ┆ ---   ┆ ame        ┆ ---        │
│ datetime[μs ┆ str         ┆ ---        ┆ i64        ┆   ┆ i8   ┆ u32   ┆ ---        ┆ str        │
│ , America/N ┆             ┆ str        ┆            ┆   ┆      ┆       ┆ str        ┆            │
│ ew_York]    ┆             ┆            ┆            ┆   ┆      ┆       ┆            ┆            │
╞═════════════╪═════════════╪════════════╪════════════╪═══╪══════╪═══════╪════════════╪════════════╡
│ 2025-04-10  ┆ ../image_do ┆ 2025-04-10 ┆ 1744279458 ┆ … ┆ 15   ┆ 2     ┆ Mount      ┆ https://ch │
│ 06:00:00    ┆ wnloader/im ┆            ┆            ┆   ┆      ┆       ┆ Carmel     ┆ eckthewait │
│ EDT         ┆ ages/202…   ┆            ┆            ┆   ┆      ┆       ┆ Post       ┆ .qu.edu/ca │
│             ┆             ┆            ┆            ┆   ┆      ┆       ┆ Office     ┆ …          │
│ 2025-04-10  ┆ ../image_do ┆ 2025-04-10 ┆ 1744279521 ┆ … ┆ 15   ┆ 2     ┆ Mount      ┆ https://ch │
│ 06:05:00    ┆ wnloader/im ┆            ┆            ┆   ┆      ┆       ┆ Carmel     ┆ eckthewait │
│ EDT         ┆ ages/202…   ┆            ┆            ┆   ┆      ┆       ┆ Post       ┆ .qu.edu/ca │
│             ┆             ┆            ┆            ┆   ┆      ┆       ┆ Office     ┆ …          │
│ 2025-04-10  ┆ ../image_do ┆ 2025-04-10 ┆ 1744279963 ┆ … ┆ 15   ┆ 1     ┆ Mount      ┆ https://ch │
│ 06:10:00    ┆ wnloader/im ┆            ┆            ┆   ┆      ┆       ┆ Carmel     ┆ eckthewait │
│ EDT         ┆ ages/202…   ┆            ┆            ┆   ┆      ┆       ┆ Post       ┆ .qu.edu/ca │
│             ┆             ┆            ┆            ┆   ┆      ┆       ┆ Office     ┆ …          │
│ 2025-04-10  ┆ ../image_do ┆ 2025-04-10 ┆ 1744280121 ┆ … ┆ 15   ┆ 1     ┆ Mount      ┆ https://ch │
│ 06:15:00    ┆ wnloader/im ┆            ┆            ┆   ┆      ┆       ┆ Carmel     ┆ eckthewait │
│ EDT         ┆ ages/202…   ┆            ┆            ┆   ┆      ┆       ┆ Post       ┆ .qu.edu/ca │
│             ┆             ┆            ┆            ┆   ┆      ┆       ┆ Office     ┆ …          │
│ 2025-04-10  ┆ ../image_do ┆ 2025-04-10 ┆ 1744280501 ┆ … ┆ 15   ┆ 2     ┆ Mount      ┆ https://ch │
│ 06:20:00    ┆ wnloader/im ┆            ┆            ┆   ┆      ┆       ┆ Carmel     ┆ eckthewait │
│ EDT         ┆ ages/202…   ┆            ┆            ┆   ┆      ┆       ┆ Post       ┆ .qu.edu/ca │
│             ┆             ┆            ┆            ┆   ┆      ┆       ┆ Office     ┆ …          │
└─────────────┴─────────────┴────────────┴────────────┴───┴──────┴───────┴────────────┴────────────┘

In [376]:
c = c.sort('dt')

In [377]:
import altair as alt

alt.Chart(c).mark_line().encode(
    x='dt:T',
    y='count:Q',
    # tooltip=['dt:T', 'count:Q']
    
).properties(
    width=800,
    height=400
)

alt.Chart(...)

In [378]:
traffic.select(
    pl.col('dt').dt.week()
)

shape: (964_756, 1)
┌─────┐
│ dt  │
│ --- │
│ i8  │
╞═════╡
│ 12  │
│ 12  │
│ 12  │
│ 12  │
│ 12  │
│ …   │
│ 12  │
│ 12  │
│ 12  │
│ 12  │
│ 12  │
└─────┘

In [379]:
dt(2025, 4, 10).weekday()

3

In [380]:
loc = 'MC_PO2'

t = traffic.filter(
    (pl.col('location') == loc) &
    (pl.col('dt').dt.week() == 15) &
    (pl.col('dt').dt.weekday() == 3)
)

t.group_by(
    pl.col('dt').dt.truncate('5m')
).agg(
    pl.all().sort_by('count').last()
).plot.line(
    x='dt:T',
    y='count:Q'
)

alt.Chart(...)

In [381]:
traffic.group_by(
    [pl.col('location'), pl.col('dt').dt.truncate('5m')]
).agg(
    pl.all().sort_by('count').last()
).filter(
    pl.col('location') == 'MC_PO2'
)

shape: (5_376, 10)
┌──────────┬─────────────┬─────────────┬─────────────┬───┬──────┬───────┬─────────────┬────────────┐
│ location ┆ dt          ┆ path        ┆ date_folder ┆ … ┆ week ┆ count ┆ location_na ┆ url        │
│ ---      ┆ ---         ┆ ---         ┆ ---         ┆   ┆ ---  ┆ ---   ┆ me          ┆ ---        │
│ str      ┆ datetime[μs ┆ str         ┆ str         ┆   ┆ i8   ┆ u32   ┆ ---         ┆ str        │
│          ┆ , America/N ┆             ┆             ┆   ┆      ┆       ┆ str         ┆            │
│          ┆ ew_York]    ┆             ┆             ┆   ┆      ┆       ┆             ┆            │
╞══════════╪═════════════╪═════════════╪═════════════╪═══╪══════╪═══════╪═════════════╪════════════╡
│ MC_PO2   ┆ 2025-04-13  ┆ ../image_do ┆ 2025-04-13  ┆ … ┆ 15   ┆ 10    ┆ Mount       ┆ https://ch │
│          ┆ 12:30:00    ┆ wnloader/im ┆             ┆   ┆      ┆       ┆ Carmel Post ┆ eckthewait │
│          ┆ EDT         ┆ ages/202…   ┆             ┆   ┆      ┆       ┆ Office      ┆ .qu.edu/ca │
│          ┆             ┆             ┆             ┆   ┆      ┆       ┆             ┆ …          │
│ MC_PO2   ┆ 2025-03-29  ┆ ../image_do ┆ 2025-03-29  ┆ … ┆ 13   ┆ 0     ┆ Mount       ┆ https://ch │
│          ┆ 12:25:00    ┆ wnloader/im ┆             ┆   ┆      ┆       ┆ Carmel Post ┆ eckthewait │
│          ┆ EDT         ┆ ages/202…   ┆             ┆   ┆      ┆       ┆ Office      ┆ .qu.edu/ca │
│          ┆             ┆             ┆             ┆   ┆      ┆       ┆             ┆ …          │
│ MC_PO2   ┆ 2025-03-20  ┆ ../image_do ┆ 2025-03-20  ┆ … ┆ 12   ┆ 0     ┆ Mount       ┆ https://ch │
│          ┆ 13:45:00    ┆ wnloader/im ┆             ┆   ┆      ┆       ┆ Carmel Post ┆ eckthewait │
│          ┆ EDT         ┆ ages/202…   ┆             ┆   ┆      ┆       ┆ Office      ┆ .qu.edu/ca │
│          ┆             ┆             ┆             ┆   ┆      ┆       ┆             ┆ …          │
│ MC_PO2   ┆ 2025-03-26  ┆ ../image_do ┆ 2025-03-26  ┆ … ┆ 13   ┆ 0     ┆ Mount       ┆ https://ch │
│          ┆ 17:00:00    ┆ wnloader/im ┆             ┆   ┆      ┆       ┆ Carmel Post ┆ eckthewait │
│          ┆ EDT         ┆ ages/202…   ┆             ┆   ┆      ┆       ┆ Office      ┆ .qu.edu/ca │
│          ┆             ┆             ┆             ┆   ┆      ┆       ┆             ┆ …          │
│ MC_PO2   ┆ 2025-04-02  ┆ ../image_do ┆ 2025-04-02  ┆ … ┆ 14   ┆ 0     ┆ Mount       ┆ https://ch │
│          ┆ 09:25:00    ┆ wnloader/im ┆             ┆   ┆      ┆       ┆ Carmel Post ┆ eckthewait │
│          ┆ EDT         ┆ ages/202…   ┆             ┆   ┆      ┆       ┆ Office      ┆ .qu.edu/ca │
│          ┆             ┆             ┆             ┆   ┆      ┆       ┆             ┆ …          │
│ …        ┆ …           ┆ …           ┆ …           ┆ … ┆ …    ┆ …     ┆ …           ┆ …          │
│ MC_PO2   ┆ 2025-04-02  ┆ ../image_do ┆ 2025-04-02  ┆ … ┆ 14   ┆ 0     ┆ Mount       ┆ https://ch │
│          ┆ 13:35:00    ┆ wnloader/im ┆             ┆   ┆      ┆       ┆ Carmel Post ┆ eckthewait │
│          ┆ EDT         ┆ ages/202…   ┆             ┆   ┆      ┆       ┆ Office      ┆ .qu.edu/ca │
│          ┆             ┆             ┆             ┆   ┆      ┆       ┆             ┆ …          │
│ MC_PO2   ┆ 2025-03-22  ┆ ../image_do ┆ 2025-03-22  ┆ … ┆ 12   ┆ 0     ┆ Mount       ┆ https://ch │
│          ┆ 16:25:00    ┆ wnloader/im ┆             ┆   ┆      ┆       ┆ Carmel Post ┆ eckthewait │
│          ┆ EDT         ┆ ages/202…   ┆             ┆   ┆      ┆       ┆ Office      ┆ .qu.edu/ca │
│          ┆             ┆             ┆             ┆   ┆      ┆       ┆             ┆ …          │
│ MC_PO2   ┆ 2025-04-11  ┆ ../image_do ┆ 2025-04-11  ┆ … ┆ 15   ┆ 6     ┆ Mount       ┆ https://ch │
│          ┆ 18:00:00    ┆ wnloader/im ┆             ┆   ┆      ┆       ┆ Carmel Post ┆ eckthewait │
│          ┆ EDT         ┆ ages/202…   ┆             ┆   ┆      ┆       ┆ Office      ┆ .qu.edu/ca │
│          ┆             ┆             ┆  

In [ ]:
traffic.filter(
    (pl.col('dt').dt.week() == 15) &
    (pl.col('dt').dt.weekday() == 2)
).group_by()



# .with_columns(
#     time = pl.datetime(2020, 1, 1, hour=pl.col('dt').dt.hour(), minute=pl.col('dt').dt.minute()),
# ).group_by(
#     pl.col('time').dt.truncate('5m')
# ).agg(
#     pl.all().sort_by('count').last()
# ).plot.line(
#     x='time:T',
#     y='count:Q',
#     row='location_name:N'
# ).properties(
#     width=900,
# ).show()

In [412]:
# plot day 1 each camera time series across hours to find which cameras to focus on
locations = traffic['location'].unique().to_list()

chart = alt.vconcat()

for i, loc in enumerate(locations):
    location_name = cams.filter(pl.col('location') == loc).select('location_name').to_series()[0]

    chart &= traffic.filter(
        (pl.col('location') == loc) &
        (pl.col('dt').dt.date() == day.date())
    ).group_by(
        pl.col('dt').dt.truncate('5m')
    ).agg(
        pl.all().sort_by('count').last()
    ).plot.line(
        x=alt.X('dt:T', title='Time'),
        y=alt.Y('count:Q', title=location_name),
    ).properties(
        width=900,
    )

chart

alt.VConcatChart(...)

In [383]:
non_zero_traffic = traffic.group_by(
    [pl.col('location'), pl.col('dt').dt.date()]
).agg(
    # pl.all(),
    (pl.col('count') > 0).sum().alias('non_zero_count'),
)

non_zero_traffic.head()

shape: (5, 3)
┌───────────┬────────────┬────────────────┐
│ location  ┆ dt         ┆ non_zero_count │
│ ---       ┆ ---        ┆ ---            │
│ str       ┆ date       ┆ u32            │
╞═══════════╪════════════╪════════════════╡
│ NH_DH     ┆ 2025-04-05 ┆ 763            │
│ MC_DHPOS  ┆ 2025-03-27 ┆ 0              │
│ NH_DHPOS3 ┆ 2025-03-19 ┆ 0              │
│ MC_PO     ┆ 2025-03-30 ┆ 1804           │
│ MC_Exit1  ┆ 2025-03-17 ┆ 0              │
└───────────┴────────────┴────────────────┘

In [384]:
traffic.head()

shape: (5, 10)
┌─────────────┬─────────────┬────────────┬────────────┬───┬──────┬───────┬────────────┬────────────┐
│ path        ┆ date_folder ┆ timestamp  ┆ location   ┆ … ┆ week ┆ count ┆ location_n ┆ url        │
│ ---         ┆ ---         ┆ ---        ┆ ---        ┆   ┆ ---  ┆ ---   ┆ ame        ┆ ---        │
│ str         ┆ str         ┆ i64        ┆ str        ┆   ┆ i8   ┆ u32   ┆ ---        ┆ str        │
│             ┆             ┆            ┆            ┆   ┆      ┆       ┆ str        ┆            │
╞═════════════╪═════════════╪════════════╪════════════╪═══╪══════╪═══════╪════════════╪════════════╡
│ ../image_do ┆ 2025-03-19  ┆ 1742390088 ┆ NH_DHDeli  ┆ … ┆ 12   ┆ 0     ┆ North      ┆ https://ch │
│ wnloader/im ┆             ┆            ┆            ┆   ┆      ┆       ┆ Haven      ┆ eckthewait │
│ ages/202…   ┆             ┆            ┆            ┆   ┆      ┆       ┆ Dining     ┆ .qu.edu/ca │
│             ┆             ┆            ┆            ┆   ┆      ┆       ┆ Hall Deli  ┆ …          │
│ ../image_do ┆ 2025-03-19  ┆ 1742389519 ┆ MC_Exit2   ┆ … ┆ 12   ┆ 0     ┆ Mount      ┆ https://ch │
│ wnloader/im ┆             ┆            ┆            ┆   ┆      ┆       ┆ Carmel     ┆ eckthewait │
│ ages/202…   ┆             ┆            ┆            ┆   ┆      ┆       ┆ Exit       ┆ .qu.edu/ca │
│             ┆             ┆            ┆            ┆   ┆      ┆       ┆            ┆ …          │
│ ../image_do ┆ 2025-03-19  ┆ 1742384680 ┆ MC_PO      ┆ … ┆ 12   ┆ 2     ┆ Mount      ┆ https://ch │
│ wnloader/im ┆             ┆            ┆            ┆   ┆      ┆       ┆ Carmel     ┆ eckthewait │
│ ages/202…   ┆             ┆            ┆            ┆   ┆      ┆       ┆ Post       ┆ .qu.edu/ca │
│             ┆             ┆            ┆            ┆   ┆      ┆       ┆ Office     ┆ …          │
│ ../image_do ┆ 2025-03-19  ┆ 1742380850 ┆ MC_DHServi ┆ … ┆ 12   ┆ 1     ┆ Mount      ┆ https://ch │
│ wnloader/im ┆             ┆            ┆ ce1        ┆   ┆      ┆       ┆ Carmel     ┆ eckthewait │
│ ages/202…   ┆             ┆            ┆            ┆   ┆      ┆       ┆ Dining     ┆ .qu.edu/ca │
│             ┆             ┆            ┆            ┆   ┆      ┆       ┆ Hall       ┆ …          │
│ ../image_do ┆ 2025-03-19  ┆ 1742422697 ┆ NH_DHGym   ┆ … ┆ 12   ┆ 0     ┆ North      ┆ https://ch │
│ wnloader/im ┆             ┆            ┆            ┆   ┆      ┆       ┆ Haven      ┆ eckthewait │
│ ages/202…   ┆             ┆            ┆            ┆   ┆      ┆       ┆ Dining     ┆ .qu.edu/ca │
│             ┆             ┆            ┆            ┆   ┆      ┆       ┆ Hall Gym   ┆ …          │
└─────────────┴─────────────┴────────────┴────────────┴───┴──────┴───────┴────────────┴────────────┘

In [385]:
counts_pivot = traffic.with_columns([
    pl.col('dt').dt.truncate('5m').alias('dt_5min')
]).pivot(
    values='count',
    index='dt_5min',
    on='location',
    aggregate_function='max'
).sort('dt_5min')

counts_pivot

shape: (5_379, 20)
┌──────────────────────┬───────────┬──────────┬───────┬───┬────────┬───────────┬───────┬───────────┐
│ dt_5min              ┆ NH_DHDeli ┆ MC_Exit2 ┆ MC_PO ┆ … ┆ MC_PO2 ┆ MC_Piazza ┆ NH_DH ┆ NH_DHPOS1 │
│ ---                  ┆ ---       ┆ ---      ┆ ---   ┆   ┆ ---    ┆ ---       ┆ ---   ┆ ---       │
│ datetime[μs,         ┆ u32       ┆ u32      ┆ u32   ┆   ┆ u32    ┆ u32       ┆ u32   ┆ u32       │
│ America/New_York]    ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
╞══════════════════════╪═══════════╪══════════╪═══════╪═══╪════════╪═══════════╪═══════╪═══════════╡
│ 2025-03-17 06:00:00  ┆ 0         ┆ 0        ┆ 2     ┆ … ┆ 0      ┆ 0         ┆ 0     ┆ 0         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
│ 2025-03-17 06:05:00  ┆ 0         ┆ 0        ┆ 2     ┆ … ┆ 0      ┆ 0         ┆ 0     ┆ 0         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
│ 2025-03-17 06:10:00  ┆ 0         ┆ 0        ┆ 2     ┆ … ┆ 0      ┆ 0         ┆ 0     ┆ 0         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
│ 2025-03-17 06:15:00  ┆ 0         ┆ 0        ┆ 2     ┆ … ┆ 0      ┆ 0         ┆ 0     ┆ 0         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
│ 2025-03-17 06:20:00  ┆ 0         ┆ 0        ┆ 2     ┆ … ┆ 0      ┆ 0         ┆ 0     ┆ 0         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
│ …                    ┆ …         ┆ …        ┆ …     ┆ … ┆ …      ┆ …         ┆ …     ┆ …         │
│ 2025-04-13 21:35:00  ┆ 0         ┆ 0        ┆ 7     ┆ … ┆ 2      ┆ 0         ┆ 1     ┆ 0         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
│ 2025-04-13 21:40:00  ┆ 0         ┆ 0        ┆ 7     ┆ … ┆ 2      ┆ 0         ┆ 1     ┆ 0         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
│ 2025-04-13 21:45:00  ┆ 0         ┆ 0        ┆ 7     ┆ … ┆ 2      ┆ 0         ┆ 0     ┆ 0         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
│ 2025-04-13 21:50:00  ┆ 0         ┆ 0        ┆ 8     ┆ … ┆ 2      ┆ 0         ┆ 0     ┆ 0         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
│ 2025-04-13 21:55:00  ┆ 0         ┆ 0        ┆ 7     ┆ … ┆ 2      ┆ 0         ┆ 0     ┆ 0         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
└──────────────────────┴───────────┴──────────┴───────┴───┴────────┴───────────┴───────┴───────────┘

In [386]:
counts_pivot.filter(
    # (pl.col('dt_5min').dt.week() == 12) &
    # (pl.col('dt_5min').dt.weekday() == 1)

    (pl.col('dt_5min').dt.week() == 15) &
    (pl.col('dt_5min').dt.weekday() == 3)
)

shape: (192, 20)
┌──────────────────────┬───────────┬──────────┬───────┬───┬────────┬───────────┬───────┬───────────┐
│ dt_5min              ┆ NH_DHDeli ┆ MC_Exit2 ┆ MC_PO ┆ … ┆ MC_PO2 ┆ MC_Piazza ┆ NH_DH ┆ NH_DHPOS1 │
│ ---                  ┆ ---       ┆ ---      ┆ ---   ┆   ┆ ---    ┆ ---       ┆ ---   ┆ ---       │
│ datetime[μs,         ┆ u32       ┆ u32      ┆ u32   ┆   ┆ u32    ┆ u32       ┆ u32   ┆ u32       │
│ America/New_York]    ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
╞══════════════════════╪═══════════╪══════════╪═══════╪═══╪════════╪═══════════╪═══════╪═══════════╡
│ 2025-04-09 06:00:00  ┆ 0         ┆ 0        ┆ 4     ┆ … ┆ 1      ┆ 0         ┆ 0     ┆ 0         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
│ 2025-04-09 06:05:00  ┆ 1         ┆ 0        ┆ 4     ┆ … ┆ 1      ┆ 0         ┆ 0     ┆ 1         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
│ 2025-04-09 06:10:00  ┆ 0         ┆ 0        ┆ 4     ┆ … ┆ 1      ┆ 0         ┆ 0     ┆ 1         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
│ 2025-04-09 06:15:00  ┆ 2         ┆ 0        ┆ 4     ┆ … ┆ 1      ┆ 0         ┆ 0     ┆ 0         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
│ 2025-04-09 06:20:00  ┆ 0         ┆ 0        ┆ 4     ┆ … ┆ 1      ┆ 0         ┆ 0     ┆ 0         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
│ …                    ┆ …         ┆ …        ┆ …     ┆ … ┆ …      ┆ …         ┆ …     ┆ …         │
│ 2025-04-09 21:35:00  ┆ 0         ┆ 1        ┆ 6     ┆ … ┆ 4      ┆ 0         ┆ 2     ┆ 0         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
│ 2025-04-09 21:40:00  ┆ 0         ┆ 0        ┆ 6     ┆ … ┆ 3      ┆ 0         ┆ 0     ┆ 0         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
│ 2025-04-09 21:45:00  ┆ 0         ┆ 0        ┆ 5     ┆ … ┆ 3      ┆ 0         ┆ 0     ┆ 1         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
│ 2025-04-09 21:50:00  ┆ 0         ┆ 0        ┆ 6     ┆ … ┆ 2      ┆ 0         ┆ 0     ┆ 0         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
│ 2025-04-09 21:55:00  ┆ 1         ┆ 0        ┆ 6     ┆ … ┆ 4      ┆ 0         ┆ 0     ┆ 0         │
│ EDT                  ┆           ┆          ┆       ┆   ┆        ┆           ┆       ┆           │
└──────────────────────┴───────────┴──────────┴───────┴───┴────────┴───────────┴───────┴───────────┘

In [387]:
counts_pivot.group_by(
    pl.col('dt_5min').dt.week()
).len()

shape: (4, 2)
┌─────────┬──────┐
│ dt_5min ┆ len  │
│ ---     ┆ ---  │
│ i8      ┆ u32  │
╞═════════╪══════╡
│ 12      ┆ 1344 │
│ 15      ┆ 1347 │
│ 13      ┆ 1344 │
│ 14      ┆ 1344 │
└─────────┴──────┘

In [388]:
counts_pivot.filter(
    # (pl.col('dt_5min').dt.week() == 12) &
    # (pl.col('dt_5min').dt.weekday() == 1)

    (pl.col('dt_5min').dt.week() == 15) &
    (pl.col('dt_5min').dt.weekday() == 3)
).plot.line(
    x='dt_5min:T',
    y='tot_count:Q',
    # y='MC_PO2:Q',
).properties(
    width=900,
)

alt.Chart(...)

In [389]:
counts_pivot = counts_pivot.with_columns(
    tot_count = pl.sum_horizontal(pl.all().exclude('dt_5min'))
)
counts_pivot

shape: (5_379, 21)
┌───────────────────┬───────────┬──────────┬───────┬───┬───────────┬───────┬───────────┬───────────┐
│ dt_5min           ┆ NH_DHDeli ┆ MC_Exit2 ┆ MC_PO ┆ … ┆ MC_Piazza ┆ NH_DH ┆ NH_DHPOS1 ┆ tot_count │
│ ---               ┆ ---       ┆ ---      ┆ ---   ┆   ┆ ---       ┆ ---   ┆ ---       ┆ ---       │
│ datetime[μs,      ┆ u32       ┆ u32      ┆ u32   ┆   ┆ u32       ┆ u32   ┆ u32       ┆ u32       │
│ America/New_York] ┆           ┆          ┆       ┆   ┆           ┆       ┆           ┆           │
╞═══════════════════╪═══════════╪══════════╪═══════╪═══╪═══════════╪═══════╪═══════════╪═══════════╡
│ 2025-03-17        ┆ 0         ┆ 0        ┆ 2     ┆ … ┆ 0         ┆ 0     ┆ 0         ┆ 7         │
│ 06:00:00 EDT      ┆           ┆          ┆       ┆   ┆           ┆       ┆           ┆           │
│ 2025-03-17        ┆ 0         ┆ 0        ┆ 2     ┆ … ┆ 0         ┆ 0     ┆ 0         ┆ 7         │
│ 06:05:00 EDT      ┆           ┆          ┆       ┆   ┆           ┆       ┆           ┆           │
│ 2025-03-17        ┆ 0         ┆ 0        ┆ 2     ┆ … ┆ 0         ┆ 0     ┆ 0         ┆ 7         │
│ 06:10:00 EDT      ┆           ┆          ┆       ┆   ┆           ┆       ┆           ┆           │
│ 2025-03-17        ┆ 0         ┆ 0        ┆ 2     ┆ … ┆ 0         ┆ 0     ┆ 0         ┆ 7         │
│ 06:15:00 EDT      ┆           ┆          ┆       ┆   ┆           ┆       ┆           ┆           │
│ 2025-03-17        ┆ 0         ┆ 0        ┆ 2     ┆ … ┆ 0         ┆ 0     ┆ 0         ┆ 7         │
│ 06:20:00 EDT      ┆           ┆          ┆       ┆   ┆           ┆       ┆           ┆           │
│ …                 ┆ …         ┆ …        ┆ …     ┆ … ┆ …         ┆ …     ┆ …         ┆ …         │
│ 2025-04-13        ┆ 0         ┆ 0        ┆ 7     ┆ … ┆ 0         ┆ 1     ┆ 0         ┆ 14        │
│ 21:35:00 EDT      ┆           ┆          ┆       ┆   ┆           ┆       ┆           ┆           │
│ 2025-04-13        ┆ 0         ┆ 0        ┆ 7     ┆ … ┆ 0         ┆ 1     ┆ 0         ┆ 12        │
│ 21:40:00 EDT      ┆           ┆          ┆       ┆   ┆           ┆       ┆           ┆           │
│ 2025-04-13        ┆ 0         ┆ 0        ┆ 7     ┆ … ┆ 0         ┆ 0     ┆ 0         ┆ 16        │
│ 21:45:00 EDT      ┆           ┆          ┆       ┆   ┆           ┆       ┆           ┆           │
│ 2025-04-13        ┆ 0         ┆ 0        ┆ 8     ┆ … ┆ 0         ┆ 0     ┆ 0         ┆ 13        │
│ 21:50:00 EDT      ┆           ┆          ┆       ┆   ┆           ┆       ┆           ┆           │
│ 2025-04-13        ┆ 0         ┆ 0        ┆ 7     ┆ … ┆ 0         ┆ 0     ┆ 0         ┆ 10        │
│ 21:55:00 EDT      ┆           ┆          ┆       ┆   ┆           ┆       ┆           ┆           │
└───────────────────┴───────────┴──────────┴───────┴───┴───────────┴───────┴───────────┴───────────┘

In [390]:
# print all unique weeks
counts_pivot['dt_5min'].dt.week().unique().to_list()

[12, 13, 14, 15]

In [391]:
counts_pivot.filter(
    (pl.col('dt_5min').dt.week() == 12) &
    (pl.col('dt_5min').dt.weekday() == 1)
).plot.line(
    x='dt_5min:T',
    y=alt.Y(
        'tot_count:Q',
        scale=alt.Scale(domain=[0, 25])
    ),
)

alt.Chart(...)

In [392]:
counts_pivot = counts_pivot.filter(
    pl.col('dt_5min').dt.week() >= 14
)

counts_pivot = counts_pivot.with_columns(
    week = pl.col('dt_5min').dt.week(),
    time = pl.datetime(2020, 1, 1, hour=pl.col('dt_5min').dt.hour(), minute=pl.col('dt_5min').dt.minute()),
)

chart = alt.Chart(counts_pivot).mark_line().encode(
    x = alt.X('time:T', title='Time'),
    y = alt.Y('tot_count:Q', title='Total Count'),
).facet(
    row=alt.Row('week:O', title='Week', sort='ascending'),
    column=alt.Column('day(dt_5min):O', title='Day', sort=['Mon', 'Tue', 'Wed', 'Thu', 'Fri', 'Sat', 'Sun']),
)

chart

alt.FacetChart(...)

In [413]:
traffic.filter(
    pl.col('dt').dt.week() >= 14
).group_by(
    pl.col('dt').dt.date()
).agg(
    pl.col('count').sum().alias('total_count'),
).sort(
    pl.col('dt').dt.date()
).plot.line(
    x=alt.X('dt:T', title='Date'),
    y=alt.Y('total_count:Q', title='Total Count'),
).properties(
    width=900,
    height=400
)

alt.Chart(...)

In [285]:
locations

['MC_DHPOS',
 'MC_PO2',
 'MC_DHSmoothies',
 'MC_Exit1',
 'NH_DHPOS2',
 'MC_PO',
 'NH_DHPOS3',
 'MC_Exit2',
 'MC_DHService2',
 'MC_Piazza',
 'MC_RLSHAKE',
 'MC_DHService1',
 'MC_Turnstiles',
 'NH_DHDeli',
 'NH_DHService2',
 'NH_DHPOS1',
 'NH_DHGym',
 'NH_DH',
 'NH_DHService3']

In [287]:
chart = alt.Chart(counts_pivot).mark_line().encode(
    x = alt.X('time:T', title='Time'),
    y = alt.Y('MC_PO2:Q', title='Total Count'),
).facet(
    row=alt.Row('week:O', title='Week', sort='ascending'),
    column=alt.Column('day(dt_5min):O', title='Day', sort=['Mon', 'Tue', 'Wed', 'Thu', 'Fri', 'Sat', 'Sun']),
)

chart

alt.FacetChart(...)

In [ ]:
chart = alt.Chart(counts_pivot).mark_line().encode(
    x = alt.X('time:T', title='Time'),
    y = alt.Y('row:Q', title='Total Count'),
).repeat(
    row=alt.Row('week:O', title='Week', sort='ascending'),
    column=alt.Column('day(dt_5min):O', title='Day', sort=['Mon', 'Tue', 'Wed', 'Thu', 'Fri', 'Sat', 'Sun']),
)

chart